# Deliverable 3. Create a Travel Itinerary Map

----

1. Create a folder called `Vacation_Itinerary` to store all the files for this deliverable.

2. Download the `Vacation_Itinerary_starter_code.ipynb` file into your `Vacation_Itinerary` folder and rename it `Vacation_Itinerary.ipynb`.

3. Make sure the initial dependencies and the Geoapify API key are imported.

4. From your `Vacation_Search` folder from Deliverable 2, import the `WeatherPy_vacation.csv` file as a DataFrame named `vacation_df`.

5. Use GeoViews to create a map that shows all the cities in the `vacation_df` DataFrame. Configure the map as follows:

    * The point's size should be the maximum temperature for the city

    * The point's color should be the city's name

    * Use the `hover_cols` parameter to the the "Hotel Name", "Country", and "Current Description" columns to each point as additional information.

6. From the map, *choose four cities* that a customer might want to visit. They should be close together and in the same country. Use the `loc` method to create separate DataFrames for each city on the travel route.

    > **Hint:** You will start and end the route in the same city, so the `vacation_start` and `vacation_end` DataFrames will be in the same city.

7. Use the Pandas `concat` function to merge the DataFrame from each city in the itinerary to create a new DataFrame named `itinerary_df` to store the itinerary details.

8. Use the Pandas `copy` function to create a new DataFrame named `waypoints_df` to store the longitude and latitude for each city in `itinerary_df`.

    > **Hint:** You'll use this DataFrame to create a map using GeoViews, so recall that the first column should be the longitude, and the second the latitude.

9. Use GeoViews to create a map that shows the four cities in the itinerary.

10. Next, you'll use the Geoapify Routing API to find a route between the cities in the itinerary. Review the code that sets the initial parameters and fetches the coordinates from each city to define the `waypoints` parameter by using a `for` loop.

    > **Hint:** You can note that the `mode` parameter is set to `drive`, you can play around with other modes as it's shown in [the "Travel modes" table](https://apidocs.geoapify.com/docs/routing/#api) in the Geoapify Routing API documentation.

11. Use the Geoapify Routing API to retrieve the route's directions for your itinerary.

12. From the JSON response, store the route's legs coordinates in a variable called `legs`.

13. Loop through the route legs coordinates to fetch the latitude and longitude for each step. Store the latitude and longitude values into two Python lists named `longitude` and `latitude`.

14. Use the `longitude` and `latitude` Python lists to create a new DataFrame named `route_df`.

15. Use the GeoViews `Path` function to configure a line plot by using `route_df`. Set a custom color and width for the line that may contrast with the map.

16. Use the asterisk operator to display a composed plot that shows the itinerary's route over the map containing the cities. 

17. Save your map to the `Vacation_Itinerary` folder as `WeatherPy_travel_map.png`.

---

## Make sure the initial dependencies and the Geoapify API key are imported

In [1]:
# Dependencies and Setup
import geoviews as gv
import hvplot.pandas
import pandas as pd
import requests

# Turn off warning messages
import warnings
warnings.filterwarnings("ignore")

# Import API key
from config import geoapify_key

## From your `Vacation_Search` folder from Deliverable 2, import the `WeatherPy_vacation.csv` file as a DataFrame named `vacation_df`

In [2]:
# Read the WeatherPy_vacation.csv into a DataFrame
vacation_df = pd.read_csv("../Vacation_Search/Weatherpy_vacation.csv")

# Display sample data
vacation_df.head()

City_ID        City Country  Max Temp Current Description      Lat  \
0        2       Vaini      TO     78.96    scattered clouds -21.2000   
1        4        Chuy      UY     76.15     overcast clouds -33.6971   
2       12      Kupang      ID     79.14     overcast clouds -10.1667   
3       21  Port Blair      IN     80.64                mist  11.6667   
4       33        Atar      MR     70.11           clear sky  20.5169   

        Lng                   Hotel Name  
0 -175.2000  Keleti International Resort  
1  -53.4616                      Alerces  
2  123.5833       BIB & LANG GUEST HOUSE  
3   92.7500         Andaman Ocean Breeze  
4  -13.0499                   فندق سكليل

## Use GeoViews to create a map that shows all the cities in the `vacation_df` DataFrame. Configure the map as follows:

* The point's size should be the maximum temperature for the city

* The point's color should be the city's name

* Use the `hover_cols` parameter to the the "Hotel Name", "Country", and "Current Description" columns to each point as additional information.

In [3]:
# Configure the map plot
map_plot = vacation_df.hvplot.points('Lng', 'Lat',
                                     geo = True, tiles = 'OSM',
                                     frame_width = 600, 
                                     frame_height = 400, 
                                     color = 'City', 
                                     size = 'Max Temp',
                                     scale = 0.7,
                                     hover_cols = ['Hotel Name', 'Country', 'Current Description'])

# Display the map
map_plot

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]   (City,Max Temp,Hotel Name,Country,Current Description)

## From the map, *choose four cities* that a customer might want to visit. They should be close together and in the same country. Use the `loc` method to create separate DataFrames for each city on the travel route.

In [25]:
# Create DataFrames for each city by filtering the 'vacation_df' using the loc method
vacation_start = vacation_df.loc[vacation_df['City'] == 'Padang']
vacation_end = vacation_df.loc[vacation_df['City'] == 'Padang']
vacation_stop1 = vacation_df.loc[vacation_df['City'] == 'Meulaboh']
vacation_stop2 = vacation_df.loc[vacation_df['City'] == 'Sibolga']
vacation_stop3 = vacation_df.loc[vacation_df['City'] == 'Lhokseumawe']

## Use the Pandas `concat` function to merge the DataFrame from each city in the itinerary to create a new DataFrame named `itinerary_df` to store the itinerary details

In [26]:
# Use the Pandas concat function to create a new DataFrame to store the itinerary details.
itinerary_df = pd.concat([vacation_start, 
                         vacation_stop1, 
                         vacation_stop2,
                         vacation_stop3,
                         vacation_end], 
                        ignore_index = True)

# Display sample data
itinerary_df

City_ID         City Country  Max Temp Current Description     Lat  \
0      302       Padang      ID     77.40     overcast clouds -0.9492   
1      530     Meulaboh      ID     76.77     overcast clouds  4.1363   
2      638      Sibolga      ID     75.67     overcast clouds  1.7427   
3      443  Lhokseumawe      ID     76.62     overcast clouds  5.1801   
4      302       Padang      ID     77.40     overcast clouds -0.9492   

        Lng         Hotel Name  
0  100.3543       losmen Surya  
1   96.1285     Hotel Meuligou  
2   98.7792  Hotel Prima Indah  
3   97.1507    Vina Vira Hotel  
4  100.3543       losmen Surya

## Use the Pandas `copy` function to create a new DataFrame named `waypoints_df` to store the longitude and latitude for each city in `itinerary_df`

In [27]:
# Create a Pandas DataFrame to store the latitude and longitude for each city in the itineray
waypoints_df = itinerary_df[['Lng', 'Lat']].copy()

# Display sample data
waypoints_df

Lng     Lat
0  100.3543 -0.9492
1   96.1285  4.1363
2   98.7792  1.7427
3   97.1507  5.1801
4  100.3543 -0.9492

## Use GeoViews to create map that shows the four cities in the itinerary

In [52]:
# Configure the map plot by using the itineraty_df
waypoints_map = itinerary_df.hvplot.points('Lng', 'Lat',
                                          geo = True, tiles = 'OSM',
                                          color = 'City', 
                                          frame_width = 700, 
                                          frame_height = 500, 
                                          scale = 1.5, 
                                          size = 'Max Temp')

In [53]:
# Display the route_map
waypoints_map

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]   (City,Max Temp)

## Next, you'll use the Geoapify Routing API to find a route between the cities in the itinerary. Review the code that sets the initial parameters and fetches the coordinates from each city to define the `waypoints` parameter by using a `for` loop

In [54]:
# Set parameters to trace the route
radius = 5000
params = {
    "mode":"drive",
    "apiKey": geoapify_key,
}

In [55]:
# Set an empty waypoints String variable
waypoints = ""

# Iterate through the route_df DataFrame to define the waypoints
for index, row in waypoints_df.iterrows():
    waypoints = waypoints + str(row["Lat"]) + "," + str(row["Lng"]) + "|"

# Delete the last character from the string
waypoints = waypoints[:-1]

# Add the waypoints to the params dictionary
params["waypoints"] = waypoints

# Display the params dictionary
params

{'mode': 'drive',
 'apiKey': '8835c69727014bf5846bfa4d7b0633ff',
 'waypoints': '-0.9492,100.3543|4.1363,96.1285|1.7427,98.7792|5.1801,97.1507|-0.9492,100.3543'}

## Use the Geoapify Routing API to retrieve the route's directions for your itinerary

In [60]:
# Set up the base URL for the Geoapify Places API.
base_url = "https://api.geoapify.com/v1/routing"

# Make request and retrieve the JSON data by using the params dictionaty
route_response = requests.get(base_url, params=params)

# Convert the API response to JSON format
route_response = route_response.json()


## From the JSON response, store the route's legs coordinates in a variable called `legs`

In [61]:
# Fetch the route's legs coordinates from the JSON reponse
legs = route_response['features'][0]['geometry']['coordinates']

## Loop through the route legs coordinates to fetch the latitude and longitude for each step. Store the latitude and longitude value into two Python lists names `longitude` and `latitude`

In [62]:
# Create and empty list to store the longitude of each step
longitude = []

# Create and empty list to store the latitude of step
latitude = []

# Loop through the legs coordinates to fetch the latitude and longitude for each step
for leg in legs: 
    for coordinate in leg:
        longitude.append(coordinate[0])
        latitude.append(coordinate[1])

## Use the `longitude` and `latitude` Python lists to create a new DataFrame named `route_df`

In [63]:
# Create an empty DataFrame to store the steps' coordinates
route_df = pd.DataFrame()

# Add the steps' longitude and latitude from each step as columns to the DataFrame
route_df['Longitude'] = longitude
route_df['Latitude'] = latitude 

# Display sample data
route_df.head()

Longitude  Latitude
0  100.354211 -0.949044
1  100.354167 -0.949063
2  100.354137 -0.949076
3  100.354124 -0.949083
4  100.354111 -0.949094

##  Use the GeoViews `Path` function to configure a line plot by using `route_df`. Set a custom color and width for the line that may contrast with the map

In [64]:
# Configure the route path by using the GeoViews' Path function
route_path = gv.Path(route_df,).opts(
    height=500,
    width=700,
    line_width = 3,
    color = "red")

In [65]:
# Display a composed plot by using the route_map and route_path objects
waypoints_map * route_path

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]   (City,Max Temp)
   .Path.I   :Path   [Longitude,Latitude]